# Huggingface 로그인

In [ ]:
# 신청이 승인되면 계정 settings 페이지에서 access token 복사하여 사용
huggingface-cli login

# 패키지 설치

In [ ]:
pip install transformers
pip install chromadb
pip install torch

# import

In [ ]:
from dateutil.parser import parse
import pandas as pd

import chromadb

import torch
import transformers
from transformers import AutoTokenizer, AutoModel

# 시드 고정

In [ ]:
def seed_everything(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed) # if use multi-GPU
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)

seed_everything(42)

# DB 연결

In [ ]:
client = chromadb.Client()
word_test = client.create_collection(name="excel_test")

# 모델 로드

In [ ]:
# 임베딩 모델 로드
tokenizer = AutoTokenizer.from_pretrained("bespin-global/klue-sroberta-base-continue-learning-by-mnr")
model = AutoModel.from_pretrained("bespin-global/klue-sroberta-base-continue-learning-by-mnr")

# LLM 모델 로드
model_id = "meta-llama/Meta-Llama-3-8B-Instruct"

pipeline = transformers.pipeline("text-generation",
                                 model=model_id,
                                 model_kwargs={"torch_dtype": torch.bfloat16},
                                 device_map="auto")

# excel 파싱 및 데이터 전처리

In [ ]:
def convert_to_date(date_str):
    if pd.isna(date_str) or date_str == '-':
        return '알 수 없음'
    elif type(date_str) == str and date_str != '-':
        return parse(date_str).strftime('%Y-%m-%d')
    else:
        return date_str.strftime('%Y-%m-%d')

In [ ]:
def table_parsing(file_path):
    df = pd.read_excel(file_path)
    
    # 데이터 전처리
    df.drop('사번',inplace=True, axis=1)
    df.rename(columns={'Unnamed: 4':'팀'}, inplace=True)
    df['팀'].fillna(df['소속'], inplace=True)
    df.rename(columns={'영문':'영문 이름'}, inplace=True)
    df['입사연월일'] = df['입사연월일'].apply(convert_to_date)
    
    txt_li = df['이름'].tolist()
    
    return df, txt_li

# Text embedding 하여 Vector DB에 저장    

In [ ]:
# 텍스트 임베딩 함수
def make_txt_emd(sentences):
    encoded_input = tokenizer(sentences, padding=True, truncation=True, return_tensors='pt')
    
    with torch.no_grad():
        model_output = model(**encoded_input)
        
    attention_mask = encoded_input['attention_mask']
    
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    sum_result = torch.sum(token_embeddings * input_mask_expanded, 1) / torch.clamp(input_mask_expanded.sum(1), min=1e-9)

    return [tensor.tolist() for tensor in sum_result]

In [ ]:
# db 저장 함수
def save_table(df, txt_emd_li, txt_li, collection):
    metadatas = []
    for i in range(len(df)):
        metadata = {'영문 이름': df.iloc[i]['영문 이름'],
                    '소속': df.iloc[i]['소속'],
                    '팀': df.iloc[i]['팀'],
                    '직책': df.iloc[i]['직책'],
                    '입사연월일': df.iloc[i]['입사연월일'],
                    '이메일': df.iloc[i]['이메일'],
                    '근무 위치': df.iloc[i]['근무 위치']}
        metadatas.append(metadata)
        collection.add(embeddings= txt_emd_li,
                       metadatas=metadatas,
                       ids=txt_li)

# 쿼리할 문장 임베딩 및 쿼리 실행

In [ ]:
# LLM 답변 생성 함수
def make_answer(context, query):
    messages = [{"role": "system", "content": context},
                {"role": "user", "content": query}]
    
    prompt = pipeline.tokenizer.apply_chat_template(messages,
                                                    tokenize=False,
                                                    add_generation_prompt=True)
    terminators = [pipeline.tokenizer.eos_token_id,
                   pipeline.tokenizer.convert_tokens_to_ids("<|eot_id|>")]
    
    outputs = pipeline(prompt,
                       max_new_tokens=512,
                       eos_token_id=terminators,
                       pad_token_id=128001,
                       do_sample=True,
                       temperature=0.2,
                       top_p=0.9)
    
    return outputs[0]["generated_text"][len(prompt):]

In [ ]:
# 쿼리
def q_and_a(user_question, collection):
    name_query = ' 라는 문장에서 정보를 알고자하는 사람의 이름이 무엇인지 답변해줘. 답변에는 질문에 대답하기위한 어떤 문장도 쓰지 말고 딱 이름만 알려줘.'
    q_name = make_answer(user_question, name_query)
    q_emd = make_txt_emd([q_name])
    
    result = collection.query(query_embeddings=q_emd[0],
                              n_results=1)
    
    q_info = result['metadatas'][0][0]
    context = f'이름: {q_name}, {q_info}'
    query = user_question + '. 답변을 생성할때는 질문에 대답하기 위한 어떤 문장도 쓰지 말고 해당되는 정답 문구만 출력해줘. 제공되지 않은 정보에 대해서는 "제공 되지 않은 정보"라고 말해줘.'
    
    print(make_answer(context, query))

# 결과

In [ ]:
file_path = '직원연락망.xlsx'
user_question = 'OOO 사원의 입사 날짜, 생일, 이메일 주소 알려줘'

# 엑셀 파일 파싱 및 전처리
df, txt_li = table_parsing(file_path)

# 임베딩 및 db에 데이터 저장
txt_emd_li = make_txt_emd(txt_li)
save_table(df, txt_emd_li, txt_li, excel_test)

# 쿼리 및 llm 답변 생성
q_and_a(user_question, excel_test)